# Ejercicio de introducción a Pytorch
Haremos un recorrido por los aspectos fundamentales de pytroch desde el manejo de tensores hasta el entrenamiento y evaluación de una red neuronal. 
Para completarlo llevamos como guía [ESTE](https://colab.research.google.com/github/phlippe/uvadlc_notebooks/blob/master/docs/tutorial_notebooks/tutorial2/Introduction_to_PyTorch.ipynb#scrollTo=u-L7YQmcHvX8) cuaderno.y otros recursos dados a lo largo del cuaderno.


Primero importamos algunas librerías básicas

In [1]:
## Standard libraries
import os
import math
import numpy as np 
import time

## Imports for plotting
import matplotlib.pyplot as plt
%matplotlib inline 
from IPython.display import set_matplotlib_formats
set_matplotlib_formats('svg', 'pdf') # For export
from matplotlib.colors import to_rgba
import seaborn as sns
sns.set()

## Progress bar
from tqdm.notebook import tqdm


In [14]:
#Pytorch libraries
import torch
import torch.nn as nn
import torch.nn.functional as F

import torchvision
import torch.utils.data
import torchvision.transforms as transforms

Primero recordemos algunas funconalidades de los tensores.

In [3]:
# Crear un tensor aleatorio de tamaño 3x3
primer_tensor = torch.rand(3, 3)

# Calcular el tamaño del tensor
tensor_size = primer_tensor.size()

# Imprimir los valores del vector y su tamaño
print(primer_tensor)
print(tensor_size)

tensor([[0.7141, 0.9062, 0.7655],
        [0.2514, 0.3411, 0.8464],
        [0.0818, 0.8722, 0.5508]])
torch.Size([3, 3])


In [7]:
# Crear una matriz de unos de tamaño 3 by 3
tensor_of_ones = torch.ones(3, 3)

# Crear una matrix identidad de tamaño 3 by 3
identity_tensor = torch.eye(3)

# Multiplicar las dos matrices anteriores
matrices_multiplied = torch.matmul(tensor_of_ones, identity_tensor)
print(matrices_multiplied)

tensor([[1., 1., 1.],
        [1., 1., 1.],
        [1., 1., 1.]])


### Cálculo de gradientes
Calculemos un gradiente utilizando Pytorch. La función está en la gráfica Graph0.

Para esto, puede ir a la sección Dynamic Computation Graph and Backpropagation, del cuaderno inicial.

In [4]:
# Initialize x, y and z to values 4, -3 and 5
x = torch.tensor(4., requires_grad=True)
y = torch.tensor(-3., requires_grad=True)
z = torch.tensor(5., requires_grad=True)

# Set q to sum of x and y, set f to product of q with z
q = x + y
f = q * z

# Compute the derivatives
f.backward()

# Print the gradients
print("Gradient of x is: " + str(x.grad))
print("Gradient of y is: " + str(y.grad))
print("Gradient of z is: " + str(z.grad))

Gradient of x is: tensor(5.)
Gradient of y is: tensor(5.)
Gradient of z is: tensor(1.)


In [5]:
print(x)

tensor(4., requires_grad=True)


Ahora calculemos los gradientes para la función descrita en la imagen Graph1

In [6]:
# Initializar x,y,z como tensores aleatorios de tamaño (1000,1000)
x = torch.rand(1000, 1000, requires_grad=True)
y = torch.rand(1000, 1000, requires_grad=True)
z = torch.rand(1000, 1000, requires_grad=True)

# Multiplicar los tensores x con y
q = torch.matmul(x, y)

# Multiplicar componente a componente los tensores z con q
f = q * z

mean_f = torch.mean(f)

# Calcular los gradientes
mean_f.backward()
print("gradient of x: ", x.grad )
print("gradient of y: ", y.grad )
print("gradient of z: ", z.grad )





gradient of x:  tensor([[0.0003, 0.0002, 0.0002,  ..., 0.0002, 0.0003, 0.0002],
        [0.0003, 0.0002, 0.0003,  ..., 0.0003, 0.0003, 0.0003],
        [0.0002, 0.0002, 0.0002,  ..., 0.0002, 0.0002, 0.0002],
        ...,
        [0.0003, 0.0002, 0.0002,  ..., 0.0002, 0.0002, 0.0002],
        [0.0003, 0.0002, 0.0002,  ..., 0.0002, 0.0003, 0.0002],
        [0.0003, 0.0003, 0.0003,  ..., 0.0003, 0.0003, 0.0002]])
gradient of y:  tensor([[0.0002, 0.0002, 0.0003,  ..., 0.0002, 0.0003, 0.0003],
        [0.0002, 0.0003, 0.0002,  ..., 0.0002, 0.0003, 0.0003],
        [0.0003, 0.0003, 0.0003,  ..., 0.0002, 0.0003, 0.0003],
        ...,
        [0.0002, 0.0002, 0.0002,  ..., 0.0002, 0.0002, 0.0003],
        [0.0002, 0.0002, 0.0002,  ..., 0.0002, 0.0002, 0.0003],
        [0.0003, 0.0003, 0.0003,  ..., 0.0002, 0.0003, 0.0003]])
gradient of z:  tensor([[0.0002, 0.0002, 0.0003,  ..., 0.0002, 0.0003, 0.0003],
        [0.0002, 0.0002, 0.0002,  ..., 0.0002, 0.0003, 0.0003],
        [0.0002, 0.0002, 0.0

### Construcción de redes neuronales con Pytorch

Construimos una red neuronal en Pytorch de forma *manual*. la entrada serán imágenes de tamaño (28,28). Es decir contienen pixeles de 784 pixeles. 
La red contendrá una capa de entrada, una capa oculta con 200 unidades y una capa de salida con 10 categorías.

In [7]:
input_layer=torch.rand(784)
# Inicializar los pesos de la red neuronal
weight_1 = torch.rand(784, requires_grad=True)
weight_2 = torch.rand(10, requires_grad=True)

# Multiplicar la capa de entrada con el peso 1
hidden_1 = torch.matmul(input_layer, weight_1)

# Multiplicar la capa oculta con el peso 2
output_layer = hidden_1 * weight_2
print(output_layer)

tensor([ 18.9799, 132.1388, 121.7150, 162.5880,   2.2027,   0.8464,  52.2410,
        119.9426,  18.4243,  68.4032], grad_fn=<MulBackward0>)


Ahora construimos la misma rede neuronal pero utilizando los módulos de Pytorch. (Ver sección *The model* del cuaderno)

In [8]:
class Net(nn.Module):
    def __init__(self, num_inputs, num_hidden, num_outputs):
        super(Net, self).__init__()
        
        # Inicializar las dos capas lineales 
        self.fc1 = nn.Linear(num_inputs, num_hidden)
        self.fc2 = nn.Linear(num_hidden, num_outputs)

    def forward(self, x):
      
        # Usar las capas inicializadas y devolver x
        x = self.fc1(x)
        x = self.fc2(x)
        return x

Construyamos la red neuronal en la gráfica NN1 dada ede forma *manual*



In [11]:
# Crear tensor aleatorio como capa de entrada
input_layer= torch.randn(4,4)

''' 
pregunta: no deberia ser 
input_layer= torch.randn(4,1, requires_grad=True)
según el esquema?
'''

# Crear matrices de pesos
weight_1= torch.randn(4, 4)
weight_2= torch.randn(4, 4)
weight_3= torch.randn(4, 4)

# Calcular la primera y segunda capa oculta

hidden_1 = torch.randn(4, 4)
hidden_2 = torch.randn(4, 4)

# Imprimir la salida
print(torch.matmul(hidden_2,weight_3))


tensor([[ 0.4574, -1.0749, -0.0413, -1.0599],
        [ 1.8267, -1.0959,  0.1196, -2.4207],
        [ 0.7548, -0.2490,  0.0394, -0.4286],
        [ 1.1255, -3.5219,  0.0782, -3.7311]])


La anterior era una red neuronal con 2 capas ocultas ocultas en donde no se aplica ninguna función no-lineal. Veamos que ésta se puede construir con una sola capa oculta.

In [12]:
# Calcular la compuesta de las matrices de pesos
weight_composed_1 = torch.matmul(weight_1,weight_2)
weight = torch.matmul(weight_composed_1,weight_3)

# Multiplicar la capa de entrada por weight e imprimir
print(torch.matmul(input_layer, weight))

tensor([[-2.0459, -2.5650, -0.2031,  3.0765],
        [-0.3768, -5.0189,  0.1364, -0.6916],
        [-0.8347, -2.9715, -0.2838,  1.4287],
        [-1.0628,  7.4094,  0.1234,  2.5732]])


## Entrenamiendo de una red neuronal para reconocimiento de dígitos (MNIST Dataset
)
### Preparar los datos

Para preparar los datos primero creamos un parámetro *transform* para transformarlos. Haremos dos cosas:
- Transformar las imágenes del MNIST Dataset a tensores para poder alimentar la red neuronal. Esto lo hacemos con el método ToTensor.
- Por otro lado, debemos normalizarlos con respecto a una media y variaza. Esto lo hacemos con el método Normalize. En este caso usaremos una media de 0.1307 y varianza de 0.3081. (Tenga en cuenta que en el MNIST Dataset los pixeles son en escala de grises, por lo cual sólo tienen un canal de código de color.)

Para componer ambas transformaciones (Convertir a tensor y normalizar) usamos transforms.Compose ver [AQUÍ](https://www.programcreek.com/python/example/104832/torchvision.transforms.Compose)


In [15]:
# Transformar los datos a tensores y normalizarlos 
transform = transforms.Compose([transforms.ToTensor(),
								transforms.Normalize((0.1307), ((0.3081)))])

Ahora definimos el conjunto de entrenamiento y testeo. Torchvision permite cargar datasets conocidos para visión como el MNIST. 
Para entender y completar los parámetros ver [AQUÍ](https://pytorch.org/vision/main/generated/torchvision.datasets.MNIST.html).

In [40]:
# Preparar el training set y testing set
trainset = torchvision.datasets.MNIST('mnist', train=True, 
									  download=True, transform=transforms.ToTensor())
testset = torchvision.datasets.MNIST('mnist',train=True, 
									  download=True, transform=transforms.ToTensor())


El método DataLoader hace parte de torch.utils.data y permite cargar los datos por lotes de un tamaño definido. Para entender los parámetros ver [AQUÍ](https://pytorch.org/docs/stable/data.html#torch.utils.data.DataLoader).
Preparar los datos para entrenamiento y testeo de manera que se procesen 32 imágenes cada vez y se barajen cada vez.

In [49]:
# Preparar training loader y testing loader. 
# Usar los parámetros dataset, batch_size, shuffle y num_workers.
trainloader = torch.utils.data.DataLoader(dataset=trainset, batch_size = 32, shuffle = True, num_workers=0)
testloader = torch.utils.data.DataLoader(dataset=testset, batch_size = 32, shuffle = True, num_workers=0)

Construya una clase para una red neuronal que será usada para entrenar el MNIST dataset. El dataset contiene imagenes de dimensiones (28,28,2), así que usted deducirá el tamaño de la capa de entrada. Para las calas ocultas use 200 unidades y para la capa de salida 10 unidades (una por cada categoría (Dígitos del 0 al 9)).
Como función de activación use Relu de manera funcional (nn.Functional ya está importado como F).


In [52]:
# Define the class Net
class Net(nn.Module):
    def __init__(self):    
    	# Define all the parameters of the net
        super(Net, self).__init__()
        self.fc1 = nn.Linear(28*28, 200)
        self.fc2 = nn.Linear(200, 10)

    def forward(self, x):   
    	# Do the forward pass
        x = F.relu(self.fc1(x))
        x = self.fc2(x)
        return x

Analize el código siguiente para la optimización del modelo, de manera que quede claro cada paso

In [53]:

model = Net()   
optimizer = torch.optim.SGD(model.parameters(), lr=0.1) # descenso de gradiente
criterion = nn.CrossEntropyLoss()  #función de costo
  
for batch_idx, data_target in enumerate(trainloader):
    print(data_target)
    data = data_target[0]  
    target = data_target[1] 
    data = data.view(-1, 28 * 28) #P3
    optimizer.zero_grad()
    
    # Complete a forward pass
    output = model(data)

    # Compute the loss, gradients and change the weights
    loss = criterion(output,target)
    loss.backward()
    optimizer.step()

[tensor([[[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]]],


        [[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]]],


        [[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]]],


        ...,


        [[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0

A continuación evaluaremos el desempeño del modelo

In [54]:
# Set the model in eval mode
model.eval()
total, correct =0,0
for i, data in enumerate(testloader, 0):
    inputs, labels = data
    
    # Put each image into a vector
    inputs = inputs.view(-1, 784)
    
    # Do the forward pass and get the predictions
    outputs = model(inputs)
    
    _, outputs = torch.max(outputs.data, 1) #mayor valor entre los dígitos.
    total += labels.size(0)
    correct += (outputs == labels).sum().item()
print('The testing set accuracy of the network is: %d %%' % (100 * correct / total))

The testing set accuracy of the network is: 94 %
